# Model Testing Pipeline

Identifying the best model (considered with best parameters of each respectively)
1.   Re-train models using both training and validation data
2.   Evaluate models against the testing data

In [3]:
!pip install ipython-autotime
%load_ext autotime

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
The autotime extension is already loaded. To reload it, use:
  %reload_ext autotime
time: 5.66 s (started: 2023-03-12 09:35:55 +00:00)


In [4]:
# Basic Libraries

import numpy as np
import pandas as pd
import seaborn as sb
import matplotlib.pyplot as plt
from datetime import datetime

from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).
time: 2.79 s (started: 2023-03-12 09:36:01 +00:00)


In [5]:
# Data Source

df = pd.read_csv("/content/drive/MyDrive/cleaned_gee_data_v3.csv")
df = df.drop(columns = ['Unnamed: 0'], axis=1)
df = df.drop(columns = ['LATITUDE', 'LONGITUDE'], axis=1)
df.head()

CO_MOL/M2  SO2_MOL/M2  NO2_MOL/M2  O3_MOL/M2  FIRE_OCCURRED
0   0.252793    0.175102    0.048868   0.390066              0
1   0.267145    0.175102    0.048868   0.390066              0
2   0.252793    0.175102    0.041340   0.390066              0
3   0.267145    0.175102    0.041340   0.390066              0
4   0.154547    0.210118    0.045284   0.550787              0

time: 630 ms (started: 2023-03-12 09:36:03 +00:00)


In [6]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 171893 entries, 0 to 171892
Data columns (total 5 columns):
 #   Column         Non-Null Count   Dtype  
---  ------         --------------   -----  
 0   CO_MOL/M2      171893 non-null  float64
 1   SO2_MOL/M2     171893 non-null  float64
 2   NO2_MOL/M2     171893 non-null  float64
 3   O3_MOL/M2      171893 non-null  float64
 4   FIRE_OCCURRED  171893 non-null  int64  
dtypes: float64(4), int64(1)
memory usage: 6.6 MB
time: 30 ms (started: 2023-03-12 09:36:04 +00:00)


In [7]:
display(df['FIRE_OCCURRED'].value_counts())

0    170544
1      1349
Name: FIRE_OCCURRED, dtype: int64

time: 5.05 ms (started: 2023-03-12 09:36:04 +00:00)


In [8]:
X = df.drop('FIRE_OCCURRED', axis=1)
y = df['FIRE_OCCURRED']

time: 5.89 ms (started: 2023-03-12 09:36:04 +00:00)


In [9]:
# Training, Testing Split

from sklearn.model_selection import train_test_split

# 90:10

X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.10, random_state=10, shuffle=True)

Original = [X_train, X_test, y_train, y_test] # For reference

time: 248 ms (started: 2023-03-12 09:36:04 +00:00)


In [10]:
if len(X_train)==len(y_train) and len(X_test) == len(y_test):
  print("X and y data length matching")
else:
  print("Error in data preparation pipeline")
print()
print("No. of training data = %d" % len(X_train))
print("No. of testing data = %d" % len(X_test))

X and y data length matching

No. of training data = 154703
No. of testing data = 17190
time: 4.01 ms (started: 2023-03-12 09:36:04 +00:00)


In [11]:
display(y_test.value_counts())

0    17059
1      131
Name: FIRE_OCCURRED, dtype: int64

time: 3.97 ms (started: 2023-03-12 09:36:04 +00:00)


In [12]:
# SMOTE

from collections import Counter
from imblearn.over_sampling import SMOTE 

print('Original dataset shape %s' % Counter(y_train))
sm = SMOTE(random_state=10)
X_train, y_train = sm.fit_resample(X_train, y_train)
print('Resampled dataset shape %s' % Counter(y_train))

Original dataset shape Counter({0: 153485, 1: 1218})
Resampled dataset shape Counter({0: 153485, 1: 153485})
time: 652 ms (started: 2023-03-12 09:36:04 +00:00)


In [13]:
# Shuffle Data since SMOTE appended many 1s at the end
# Required for some algorithms such as ANN

from sklearn.utils import shuffle

X_train, y_train = shuffle(X_train, y_train, random_state = 10)

time: 36.2 ms (started: 2023-03-12 09:36:05 +00:00)


In [14]:
# Evaluation Metrics

from sklearn.metrics import confusion_matrix, recall_score, f1_score, roc_auc_score, accuracy_score

def evaluation_metrics(y_true, y_pred):
  cfm = confusion_matrix(y_true, y_pred).ravel()
  acc = accuracy_score(y_true, y_pred)
  recs = recall_score(y_true, y_pred, average='binary')
  f1s = f1_score(y_true, y_pred, average='binary')
  rocs = roc_auc_score(y_true, y_pred, average='macro')
  return [cfm, acc, recs, f1s, rocs]

time: 1.15 ms (started: 2023-03-12 09:36:05 +00:00)


Confusion matrix format : [ tn , fp , fn , tp ]

In [15]:
# Store Model Parameters and Eval

models_final = pd.DataFrame(columns = ['model_name', 'model', 'parameters'])
models_test = pd.DataFrame(columns = ['model_name', 'confusion_matrix', 'accuracy', 'recall', 'f1_score', 'roc_auc_score'])

time: 6.56 ms (started: 2023-03-12 09:36:05 +00:00)


In [16]:
# Import ML Algorithms

from sklearn.linear_model import LogisticRegression
from sklearn.svm import SVC
from sklearn.naive_bayes import GaussianNB
from sklearn.neighbors import KNeighborsClassifier
from sklearn.ensemble import RandomForestClassifier
from sklearn.tree import DecisionTreeClassifier
from sklearn.ensemble import GradientBoostingClassifier
import xgboost
from xgboost import XGBClassifier
import lightgbm
from lightgbm import LGBMClassifier
import tensorflow as tf
from tensorflow import keras
from sklearn.ensemble import VotingClassifier

# Save Model

import pickle

time: 4.16 s (started: 2023-03-12 09:36:05 +00:00)


## Logistic Regression

- Library: Scikit-learn

**Best Parameters:**

{'warm_start': False,
 'solver': 'liblinear',
 'penalty': 'l2',
 'max_iter': 200,
 'C': 0.1}

In [17]:
name = 'log_clf'

log_clf = LogisticRegression(penalty = 'l2', 
                             warm_start = False,
                             solver = 'liblinear',
                             max_iter = 200,
                             C = 0.1,
                             n_jobs = -1, 
                             random_state = 10
                             ).fit(X_train,y_train)

y_true = y_test
y_pred = log_clf.predict(X_test)
evaluation_results = evaluation_metrics(y_true, y_pred)

models_final = models_final.append({'model_name': name, 
                        'model': log_clf, 
                        'parameters': log_clf.get_params()}, 
                        ignore_index=True)

models_test = models_test.append({'model_name': name, 
                                  'confusion_matrix' : evaluation_results[0], 
                                  'accuracy': evaluation_results[1], 
                                  'recall' : evaluation_results[2], 
                                  'f1_score': evaluation_results[3],
                                  'roc_auc_score': evaluation_results[4]}, 
                                 ignore_index=True)

/usr/local/lib/python3.9/dist-packages/sklearn/linear_model/_logistic.py:1211: UserWarning: 'n_jobs' > 1 does not have any effect when 'solver' is set to 'liblinear'. Got 'n_jobs' = 2.
  warnings.warn(


time: 819 ms (started: 2023-03-12 09:36:09 +00:00)


In [18]:
# Save Model
pickle.dump(log_clf, open('log_clf.sav', 'wb')) 

# Load Model
# log_clf = pickle.load(open('log_clf.sav', 'rb'))

time: 2.24 ms (started: 2023-03-12 09:36:10 +00:00)


## Support Vector Machine (SVM)

- Library: Scikit-learn

**Best Parameters:**

{
'kernel': 'rbf',
'C' : '4',
'class_weight'='balanced'
}

In [19]:
X_train_SVM = Original[0]
X_test_SVM = Original[1]
y_train_SVM = Original[2]
y_test_SVM = Original[3]

time: 3.79 ms (started: 2023-03-12 09:36:10 +00:00)


In [20]:
# Shuffle

X_train_SVM, y_train_SVM = shuffle(X_train_SVM, y_train_SVM, random_state = 10)

time: 27.4 ms (started: 2023-03-12 09:36:10 +00:00)


In [21]:
display(y_train_SVM.value_counts())

0    153485
1      1218
Name: FIRE_OCCURRED, dtype: int64

time: 10.6 ms (started: 2023-03-12 09:36:10 +00:00)


In [22]:
name = 'svc_clf'

svc_clf = SVC(kernel = 'rbf', 
              C = 4,
              class_weight='balanced',
              random_state = 10
              ).fit(X_train_SVM,y_train_SVM)

y_true = y_test_SVM
y_pred = svc_clf.predict(X_test_SVM)
evaluation_results = evaluation_metrics(y_true, y_pred)

models_final = models_final.append({'model_name': name, 
                        'model': svc_clf, 
                        'parameters': svc_clf.get_params()}, 
                       ignore_index=True)

models_test = models_test.append({'model_name': name, 
                                  'confusion_matrix' : evaluation_results[0], 
                                  'accuracy': evaluation_results[1], 
                                  'recall' : evaluation_results[2], 
                                  'f1_score': evaluation_results[3],
                                  'roc_auc_score': evaluation_results[4]}, 
                                 ignore_index=True)

time: 18min 13s (started: 2023-03-12 09:36:10 +00:00)


In [23]:
# Save Model
pickle.dump(svc_clf, open('svc_clf.sav', 'wb')) 

# Load Model
# svc_clf = pickle.load(open('svc_clf.sav', 'rb'))

time: 7.9 ms (started: 2023-03-12 09:54:24 +00:00)


## Naive Bayes

- Library: Scikit-learn

**Best Parameters:**

{'var_smoothing': 1e-10}

In [24]:
name = 'bayes_clf'

bayes_clf = GaussianNB(var_smoothing = 1e-10
                       ).fit(X_train,y_train)

y_true = y_test
y_pred = bayes_clf.predict(X_test)
evaluation_results = evaluation_metrics(y_true, y_pred)

models_final = models_final.append({'model_name': name, 
                        'model': bayes_clf, 
                        'parameters': bayes_clf.get_params()}, 
                       ignore_index=True)

models_test = models_test.append({'model_name': name, 
                                  'confusion_matrix' : evaluation_results[0], 
                                  'accuracy': evaluation_results[1], 
                                  'recall' : evaluation_results[2], 
                                  'f1_score': evaluation_results[3],
                                  'roc_auc_score': evaluation_results[4]}, 
                                 ignore_index=True)

time: 90.5 ms (started: 2023-03-12 09:54:24 +00:00)


In [25]:
# Save Model
pickle.dump(bayes_clf, open('bayes_clf.sav', 'wb')) 

# Load Model
# bayes_clf = pickle.load(open('bayes_clf.sav', 'rb'))

time: 1.16 ms (started: 2023-03-12 09:54:24 +00:00)


## K-Nearest Neighbor

- Library: Scikit-learn

**Best Parameters:**

{'n_neighbors': 9, 'algorithm': 'auto'}

In [26]:
name = 'neigh_clf'

neigh_clf = KNeighborsClassifier(n_neighbors = 9, 
                                 algorithm = 'auto',
                                 n_jobs = -1, 
                                 ).fit(X_train,y_train)

y_true = y_test
y_pred = neigh_clf.predict(X_test)
evaluation_results = evaluation_metrics(y_true, y_pred)

models_final = models_final.append({'model_name': name, 
                        'model': neigh_clf, 
                        'parameters': neigh_clf.get_params()}, 
                       ignore_index=True)

models_test = models_test.append({'model_name': name, 
                                  'confusion_matrix' : evaluation_results[0], 
                                  'accuracy': evaluation_results[1], 
                                  'recall' : evaluation_results[2], 
                                  'f1_score': evaluation_results[3],
                                  'roc_auc_score': evaluation_results[4]}, 
                                 ignore_index=True)

time: 936 ms (started: 2023-03-12 09:54:24 +00:00)


In [27]:
# Save Model
# pickle.dump(neigh_clf, open('neigh_clf.sav', 'wb')) 
pickle.dump(neigh_clf, open('neigh_clf.h', 'wb')) 

# Load Model
# neigh_clf = pickle.load(open('neigh_clf.sav', 'rb'))

time: 19.4 ms (started: 2023-03-12 09:54:25 +00:00)


## Decision Tree

- Library: Scikit-learn

**Best Parameters:**

{'splitter': 'random',
 'min_samples_leaf': 1,
 'max_features': 4,
 'max_depth': None,
 'criterion': 'entropy'}


In [28]:
name = 'tree_clf'

tree_clf = DecisionTreeClassifier(criterion = 'entropy', 
                                  splitter = 'random', 
                                  min_samples_leaf = 1,
                                  max_features = 4,
                                  max_depth = None,
                                  random_state = 10
                                  ).fit(X_train,y_train)

y_true = y_test
y_pred = tree_clf.predict(X_test)
evaluation_results = evaluation_metrics(y_true, y_pred)

models_final = models_final.append({'model_name': name, 
                        'model': tree_clf, 
                        'parameters': tree_clf.get_params()}, 
                       ignore_index=True)

models_test = models_test.append({'model_name': name, 
                                  'confusion_matrix' : evaluation_results[0], 
                                  'accuracy': evaluation_results[1], 
                                  'recall' : evaluation_results[2], 
                                  'f1_score': evaluation_results[3],
                                  'roc_auc_score': evaluation_results[4]}, 
                                 ignore_index=True)

time: 315 ms (started: 2023-03-12 09:54:25 +00:00)


In [29]:
# Save Model
pickle.dump(tree_clf, open('tree_clf.sav', 'wb')) 

# Load Model
# tree_clf = pickle.load(open('tree_clf.sav', 'rb'))

time: 6.28 ms (started: 2023-03-12 09:54:25 +00:00)


In [30]:
from sklearn import tree

# tree.plot_tree(tree_clf)

fig = plt.figure(figsize=(200,100))
_ = tree.plot_tree(tree_clf, 
                   feature_names=['LATITUDE','LONGITUDE','ACQ_DATE','ACQ_TIME','OPEN_TIME','CLOSE_TIME','CO_MOL/M2','SO2_MOL/M2','O2_MOL/M2','O3_MOL/M2','LOCATION','INSTRUMENT','DRY_SEASON'],
                   filled=True)

time: 21min 30s (started: 2023-03-12 09:54:25 +00:00)


## Random Forest Classifier

- Library: Scikit-learn

**Best Parameters:**

{'n_estimators': 500,
 'min_samples_split': 2,
 'min_samples_leaf': 1,
 'max_features': 3,
 'max_depth': None}

In [31]:
name = 'rnd_clf'

rnd_clf = RandomForestClassifier(n_estimators = 500, 
                                  min_samples_split = 2,
                                  min_samples_leaf = 1,
                                  max_features = 3,
                                  max_depth = None, 
                                  n_jobs = -1, 
                                  random_state = 10
                                  ).fit(X_train,y_train)

y_true = y_test
y_pred = rnd_clf.predict(X_test)
evaluation_results = evaluation_metrics(y_true, y_pred)

models_final = models_final.append({'model_name': name, 
                        'model': rnd_clf, 
                        'parameters': rnd_clf.get_params()}, 
                       ignore_index=True)

models_test = models_test.append({'model_name': name, 
                                  'confusion_matrix' : evaluation_results[0], 
                                  'accuracy': evaluation_results[1], 
                                  'recall' : evaluation_results[2], 
                                  'f1_score': evaluation_results[3],
                                  'roc_auc_score': evaluation_results[4]}, 
                                 ignore_index=True)

time: 6min 27s (started: 2023-03-12 10:15:56 +00:00)


In [32]:
# Save Model
pickle.dump(rnd_clf, open('rnd_clf.sav', 'wb')) 


# Load Model
# rnd_clf = pickle.load(open('rnd_clf.sav', 'rb'))

time: 1.25 s (started: 2023-03-12 10:22:23 +00:00)


## Gradient Boosting Classifier

- Library: Scikit-learn

**Best Parameters:**

{'n_estimators': 1000, 'max_depth': 15, 'learning_rate': 0.15}

In [33]:
name = 'gboost_clf'

gboost_clf = GradientBoostingClassifier(n_estimators = 1000, 
                                        learning_rate = 0.15, 
                                        max_depth = 15,
                                        random_state = 10
                                        ).fit(X_train,y_train)

y_true = y_test
y_pred = gboost_clf.predict(X_test)
evaluation_results = evaluation_metrics(y_true, y_pred)

models_final = models_final.append({'model_name': name, 
                        'model': gboost_clf, 
                        'parameters': gboost_clf.get_params()}, 
                       ignore_index=True)

models_test = models_test.append({'model_name': name, 
                                  'confusion_matrix' : evaluation_results[0], 
                                  'accuracy': evaluation_results[1], 
                                  'recall' : evaluation_results[2], 
                                  'f1_score': evaluation_results[3],
                                  'roc_auc_score': evaluation_results[4]}, 
                                 ignore_index=True)

time: 41min 34s (started: 2023-03-12 10:22:25 +00:00)


In [34]:
# Save Model
pickle.dump(gboost_clf, open('gboost_clf.sav', 'wb')) 
pickle.dump(gboost_clf, open('gboost_clf.h', 'wb')) 

# Load Model
# gboost_clf = pickle.load(open('gboost_clf.sav', 'rb'))

time: 1.9 s (started: 2023-03-12 11:03:59 +00:00)


## XGBoost

- Library: xgboost

**Best Parameters:**

{'n_estimators': 1000,
 'min_child_weight': 5,
 'max_depth': 15,
 'learning_rate': 0.2}

In [35]:
name = 'xgboost_clf'

xgboost_clf = XGBClassifier(n_estimators = 1000, 
                            learning_rate = 0.2,
                            max_depth = 15, 
                            min_child_weight = 5,
                            random_state = 10
                            ).fit(X_train,y_train)

y_true = y_test
y_pred = xgboost_clf.predict(X_test)
evaluation_results = evaluation_metrics(y_true, y_pred)

models_final = models_final.append({'model_name': name, 
                        'model': xgboost_clf, 
                        'parameters': xgboost_clf.get_params()}, 
                       ignore_index=True)

models_test = models_test.append({'model_name': name, 
                                  'confusion_matrix' : evaluation_results[0], 
                                  'accuracy': evaluation_results[1], 
                                  'recall' : evaluation_results[2], 
                                  'f1_score': evaluation_results[3],
                                  'roc_auc_score': evaluation_results[4]}, 
                                 ignore_index=True)

time: 10min 8s (started: 2023-03-12 11:04:01 +00:00)


In [36]:
# Save Model
pickle.dump(xgboost_clf, open('xgboost_clf_v2.sav', 'wb')) 
pickle.dump(xgboost_clf, open('xgboost_clf_v2.h', 'wb')) 

# Load Model
# xgboost_clf = pickle.load(open('xgboost_clf.sav', 'rb'))

time: 97.1 ms (started: 2023-03-12 11:14:09 +00:00)


## LightGBM

- Library: lightbgm

**Best Parameters:**

{'num_leaves': 200,
 'n_estimators': 100,
 'min_data_in_leaf': 20,
 'max_depth': 20,
 'learning_rate': 0.3}

In [37]:
name = 'lightgbm_clf'

lightgbm_clf = LGBMClassifier(n_estimators = 100, 
                              learning_rate = 0.3, 
                              max_depth = 20,
                              num_leaves = 200,
                              min_data_in_leaf = 20,
                              random_state = 10
                              ).fit(X_train,y_train)

y_true = y_test
y_pred = lightgbm_clf.predict(X_test)
evaluation_results = evaluation_metrics(y_true, y_pred)

models_final = models_final.append({'model_name': name, 
                        'model': lightgbm_clf, 
                        'parameters': lightgbm_clf.get_params()}, 
                       ignore_index=True)

models_test = models_test.append({'model_name': name, 
                                  'confusion_matrix' : evaluation_results[0], 
                                  'accuracy': evaluation_results[1], 
                                  'recall' : evaluation_results[2], 
                                  'f1_score': evaluation_results[3],
                                  'roc_auc_score': evaluation_results[4]}, 
                                 ignore_index=True)

time: 6.87 s (started: 2023-03-12 11:14:09 +00:00)


In [38]:
# Save Model
pickle.dump(lightgbm_clf, open('lightgbm_clf.sav', 'wb')) 
pickle.dump(lightgbm_clf, open('lightgbm_clf.h', 'wb')) 

# Load Model
# lightgbm_clf = pickle.load(open('lightgbm_clf.sav', 'rb'))

time: 195 ms (started: 2023-03-12 11:14:16 +00:00)


## Artificial Neural Network

- Library: Keras, Tensorflow

**Best Parameters:**
- Batch size 30
- EPOCH 50

In [39]:
tf.random.set_seed(10)

time: 1.15 ms (started: 2023-03-12 11:14:16 +00:00)


In [40]:
name = 'ann_clf'

ann_clf = keras.models.Sequential([
    keras.layers.Dense(15, input_shape=(X_train.shape[1],), activation='relu'), # No bias term
    # keras.layers.Dense(10, activation='relu'), 
    keras.layers.Dense(10, activation='relu'), 
    keras.layers.Dense(1, activation='sigmoid')
])

ann_clf.summary()

Model: "sequential"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 dense (Dense)               (None, 15)                75        
                                                                 
 dense_1 (Dense)             (None, 10)                160       
                                                                 
 dense_2 (Dense)             (None, 1)                 11        
                                                                 
Total params: 246
Trainable params: 246
Non-trainable params: 0
_________________________________________________________________
time: 467 ms (started: 2023-03-12 11:14:16 +00:00)


In [41]:
display(y_train.value_counts())

1    153485
0    153485
Name: FIRE_OCCURRED, dtype: int64

time: 14.6 ms (started: 2023-03-12 11:14:17 +00:00)


In [42]:
display(y_test.value_counts())

0    17059
1      131
Name: FIRE_OCCURRED, dtype: int64

time: 4.82 ms (started: 2023-03-12 11:14:17 +00:00)


In [43]:
ann_clf.compile(optimizer = 'adam', 
                metrics=['accuracy'], 
                loss ='binary_crossentropy')

record = ann_clf.fit(
            X_train, 
            y_train, 
            validation_data = (X_test, y_test), 
            batch_size = 30, 
            epochs = 50)

Epoch 1/50
10233/10233 [==============================] - 20s 2ms/step - loss: 0.6333 - accuracy: 0.6395 - val_loss: 0.6358 - val_accuracy: 0.5760
Epoch 2/50
10233/10233 [==============================] - 19s 2ms/step - loss: 0.5981 - accuracy: 0.6720 - val_loss: 0.6063 - val_accuracy: 0.5930
Epoch 3/50
10233/10233 [==============================] - 21s 2ms/step - loss: 0.5867 - accuracy: 0.6809 - val_loss: 0.5829 - val_accuracy: 0.5850
Epoch 4/50
10233/10233 [==============================] - 19s 2ms/step - loss: 0.5789 - accuracy: 0.6888 - val_loss: 0.5831 - val_accuracy: 0.6118
Epoch 5/50
10233/10233 [==============================] - 19s 2ms/step - loss: 0.5730 - accuracy: 0.6976 - val_loss: 0.6059 - val_accuracy: 0.5920
Epoch 6/50
10233/10233 [==============================] - 19s 2ms/step - loss: 0.5664 - accuracy: 0.7052 - val_loss: 0.5691 - val_accuracy: 0.6462
Epoch 7/50
10233/10233 [==============================] - 20s 2ms/step - loss: 0.5595 - accuracy: 0.7091 - val_loss: 0

In [44]:
y_true = y_test
prediction = ann_clf.predict(X_test)
prediction = pd.Series(prediction[:, 0])
y_pred = []

for i in range(len(prediction)):
  if prediction[i] >= 0.5:
    y_pred.append(1)
  else:
    y_pred.append(0)

evaluation_results = evaluation_metrics(y_true, y_pred)

models_final = models_final.append({'model_name': name, 
                        'model': ann_clf, 
                        'parameters': ann_clf.layers}, 
                       ignore_index=True)

models_test = models_test.append({'model_name': name, 
                                  'confusion_matrix' : evaluation_results[0], 
                                  'accuracy': evaluation_results[1], 
                                  'recall' : evaluation_results[2], 
                                  'f1_score': evaluation_results[3],
                                  'roc_auc_score': evaluation_results[4]}, 
                                 ignore_index=True)

538/538 [==============================] - 1s 1ms/step
time: 1.53 s (started: 2023-03-12 11:31:40 +00:00)


In [45]:
# Save Model
ann_clf.save('ann_clf.h5') 

# Load Model
# ann_clf = tf.keras.models.load_model('ann_clf.h5')

time: 51.8 ms (started: 2023-03-12 11:31:41 +00:00)


## Voting Classifier
- Library: Scikit-learn, Keras, Tensorflow

**Best Parameters:**

{'voting': 'hard'}

In [46]:
display(models_test)

model_name        confusion_matrix  accuracy    recall  f1_score  \
0       log_clf   [10718, 6341, 60, 71]  0.627632  0.541985  0.021703   
1       svc_clf  [10666, 6393, 27, 104]  0.626527  0.793893  0.031382   
2     bayes_clf    [8598, 8461, 37, 94]  0.505643  0.717557  0.021644   
3     neigh_clf    [16269, 790, 52, 79]  0.951018  0.603053  0.158000   
4      tree_clf    [16492, 567, 71, 60]  0.962885  0.458015  0.158311   
5       rnd_clf    [16618, 441, 65, 66]  0.970564  0.503817  0.206897   
6    gboost_clf    [16617, 442, 66, 65]  0.970448  0.496183  0.203762   
7   xgboost_clf    [16599, 460, 59, 72]  0.969808  0.549618  0.217195   
8  lightgbm_clf    [16524, 535, 48, 83]  0.966085  0.633588  0.221629   
9       ann_clf  [12405, 4654, 22, 109]  0.727981  0.832061  0.044544   

   roc_auc_score  
0       0.585137  
1       0.709567  
2       0.610786  
3       0.778372  
4       0.712389  
5       0.738983  
6       0.735137  
7       0.761327  
8       0.801113  
9       0.779622

time: 15.2 ms (started: 2023-03-12 11:31:41 +00:00)


In [47]:
print('Best Model By Accuracy')
print(models_test.loc[models_test['accuracy'] == max(models_test['accuracy'])].model_name.to_string(index=False))
print('-----------------------')
print('Best Model By Recall')
print(models_test.loc[models_test['recall'] == max(models_test['recall'])].model_name.to_string(index=False))
print('-----------------------')
print('Best Model By F1')
print(models_test.loc[models_test['f1_score'] == max(models_test['f1_score'])].model_name.to_string(index=False))
print('-----------------------')
print('Best Model By ROC')
print(models_test.loc[models_test['roc_auc_score'] == max(models_test['roc_auc_score'])].model_name.to_string(index=False))
print('-----------------------')

Best Model By Accuracy
rnd_clf
-----------------------
Best Model By Recall
ann_clf
-----------------------
Best Model By F1
lightgbm_clf
-----------------------
Best Model By ROC
lightgbm_clf
-----------------------
time: 8.24 ms (started: 2023-03-12 11:31:41 +00:00)


In [48]:
name = 'ensem_clf'

ensem_clf = VotingClassifier(estimators=[('m1', neigh_clf), ('m2', lightgbm_clf), ('m3', xgboost_clf)],
                             voting = 'hard',
                             n_jobs = -1, 
                             ).fit(X_train,y_train)

y_true = y_test
y_pred = ensem_clf.predict(X_test)
evaluation_results = evaluation_metrics(y_true, y_pred)

models_final = models_final.append({'model_name': name, 
                        'model': ensem_clf, 
                        'parameters': ensem_clf.get_params()}, 
                       ignore_index=True)

models_test = models_test.append({'model_name': name, 
                                  'confusion_matrix' : evaluation_results[0], 
                                  'accuracy': evaluation_results[1], 
                                  'recall' : evaluation_results[2], 
                                  'f1_score': evaluation_results[3],
                                  'roc_auc_score': evaluation_results[4]}, 
                                 ignore_index=True)

time: 10min 39s (started: 2023-03-12 11:31:42 +00:00)


In [49]:
# Save Model
pickle.dump(ensem_clf, open('ensem_clf.sav', 'wb')) 

# Load Model
# ensem_clf = pickle.load(open('ensem_clf.sav', 'rb'))

time: 457 ms (started: 2023-03-12 11:42:21 +00:00)


# Model Testing Result

### Results

In [50]:
# Real Model

# xgboost_clf = pickle.load(open('xgboost_clf_v2.sav', 'rb'))
# y_true = y_test

# y_pred = xgboost_clf.predict(X_test)
# cfm = confusion_matrix(y_true, y_pred).ravel()
# acc = accuracy_score(y_true, y_pred)
# recs = recall_score(y_true, y_pred, average='binary')
# f1s = f1_score(y_true, y_pred, average='binary')
# rocs = roc_auc_score(y_true, y_pred, average='macro')

# print(cfm)
# print(acc)
# print(recs)
# print(f1s)
# print(rocs)

time: 490 µs (started: 2023-03-12 11:42:21 +00:00)


In [51]:
display(models_final)

model_name                                              model  \
0        log_clf  LogisticRegression(C=0.1, max_iter=200, n_jobs...   
1        svc_clf  SVC(C=4, class_weight='balanced', random_state...   
2      bayes_clf                    GaussianNB(var_smoothing=1e-10)   
3      neigh_clf     KNeighborsClassifier(n_jobs=-1, n_neighbors=9)   
4       tree_clf  DecisionTreeClassifier(criterion='entropy', ma...   
5        rnd_clf  (DecisionTreeClassifier(max_features=3, random...   
6     gboost_clf  ([DecisionTreeRegressor(criterion='friedman_ms...   
7    xgboost_clf  XGBClassifier(base_score=None, booster=None, c...   
8   lightgbm_clf  LGBMClassifier(learning_rate=0.3, max_depth=20...   
9        ann_clf  <keras.engine.sequential.Sequential object at ...   
10     ensem_clf  VotingClassifier(estimators=[('m1',\n         ...   

                                           parameters  
0   {'C': 0.1, 'class_weight': None, 'dual': False...  
1   {'C': 4, 'break_ties': False, 'cache_size': 20...  
2            {'priors': None, 'var_smoothing': 1e-10}  
3   {'algorithm': 'auto', 'leaf_size': 30, 'metric...  
4   {'ccp_alpha': 0.0, 'class_weight': None, 'crit...  
5   {'bootstrap': True, 'ccp_alpha': 0.0, 'class_w...  
6   {'ccp_alpha': 0.0, 'criterion': 'friedman_mse'...  
7   {'objective': 'binary:logistic', 'use_label_en...  
8   {'boosting_type': 'gbdt', 'class_weight': None...  
9   [<keras.layers.core.dense.Dense object at 0x7f...  
10  {'estimators': [('m1', KNeighborsClassifier(n_...

time: 169 ms (started: 2023-03-12 11:42:21 +00:00)


In [58]:
display(models_test)

model_name        confusion_matrix  accuracy    recall  f1_score  \
0        log_clf   [10718, 6341, 60, 71]  0.627632  0.541985  0.021703   
1        svc_clf  [10666, 6393, 27, 104]  0.626527  0.793893  0.031382   
2      bayes_clf    [8598, 8461, 37, 94]  0.505643  0.717557  0.021644   
3      neigh_clf    [16269, 790, 52, 79]  0.951018  0.603053  0.158000   
4       tree_clf    [16492, 567, 71, 60]  0.962885  0.458015  0.158311   
5        rnd_clf    [16618, 441, 65, 66]  0.970564  0.503817  0.206897   
6     gboost_clf    [16617, 442, 66, 65]  0.970448  0.496183  0.203762   
7    xgboost_clf    [16599, 460, 59, 72]  0.969808  0.549618  0.217195   
8   lightgbm_clf    [16524, 535, 48, 83]  0.966085  0.633588  0.221629   
9        ann_clf  [12405, 4654, 22, 109]  0.727981  0.832061  0.044544   
10     ensem_clf    [16567, 492, 54, 77]  0.968237  0.587786  0.220000   

    roc_auc_score  
0        0.585137  
1        0.709567  
2        0.610786  
3        0.778372  
4        0.712389  
5        0.738983  
6        0.735137  
7        0.761327  
8        0.801113  
9        0.779622  
10       0.779473

time: 68.7 ms (started: 2023-03-12 11:45:22 +00:00)


In [59]:
print('Best Model By Accuracy')
print(models_test.loc[models_test['accuracy'] == max(models_test['accuracy'])].model_name.to_string(index=False))
print('-----------------------')
print('Best Model By Recall')
print(models_test.loc[models_test['recall'] == max(models_test['recall'])].model_name.to_string(index=False))
print('-----------------------')
print('Best Model By F1')
print(models_test.loc[models_test['f1_score'] == max(models_test['f1_score'])].model_name.to_string(index=False))
print('-----------------------')
print('Best Model By ROC')
print(models_test.loc[models_test['roc_auc_score'] == max(models_test['roc_auc_score'])].model_name.to_string(index=False))
print('-----------------------')

Best Model By Accuracy
rnd_clf
-----------------------
Best Model By Recall
ann_clf
-----------------------
Best Model By F1
lightgbm_clf
-----------------------
Best Model By ROC
lightgbm_clf
-----------------------
time: 17.8 ms (started: 2023-03-12 11:45:24 +00:00)


In [54]:
models_final.to_csv('models_testing.csv')
!cp models_testing.csv "drive/My Drive/"

time: 206 ms (started: 2023-03-12 11:42:22 +00:00)


In [55]:
models_test.to_csv('models_testing_eval.csv')
!cp models_testing_eval.csv "drive/My Drive/"

time: 183 ms (started: 2023-03-12 11:42:22 +00:00)


In [56]:
# result = models_test.reindex([0,1,2,3,4,5,7,6,8,9])
# result.loc[6,'model_name'] = 'xgboost_clf'
# result.loc[7,'model_name'] = 'gboost_clf'

time: 477 µs (started: 2023-03-12 11:42:22 +00:00)


In [ ]:
# print('Best Model By Accuracy')
# print(result.loc[result['accuracy'] == max(result['accuracy'])].model_name.to_string(index=False))
# print('-----------------------')
# print('Best Model By Recall')
# print(result.loc[result['recall'] == max(result['recall'])].model_name.to_string(index=False))
# print('-----------------------')
# print('Best Model By F1-Score')
# print(result.loc[result['f1_score'] == max(result['f1_score'])].model_name.to_string(index=False))
# print('-----------------------')
# print('Best Model By ROC')
# print(result.loc[result['roc_auc_score'] == max(result['roc_auc_score'])].model_name.to_string(index=False))
# print('-----------------------')

In [ ]:
# result.to_csv('model_testing_result.csv')
# !cp model_testing_result.csv "drive/My Drive/"

xgboost_clf is the most suitable model

### Model Export

In [ ]:
from google.colab import files

In [ ]:
files.download('log_clf.sav')

In [ ]:
files.download('svc_clf.sav')

In [ ]:
files.download('bayes_clf.sav')

In [ ]:
files.download('neigh_clf.sav')

In [ ]:
files.download('tree_clf.sav')

In [ ]:
files.download('rnd_clf.sav')

In [ ]:
files.download('gboost_clf.sav')

In [ ]:
files.download('xgboost_clf_v2.sav')

In [ ]:
files.download('xgboost_clf_v2.h')

In [ ]:
files.download('lightgbm_clf.sav')

In [ ]:
files.download('ann_clf.h5')